In [1]:
#Install all the Reqiuired Libraries and Packages 
import os
import glob
from tqdm import tqdm
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy.io import wavfile
from python_speech_features import mfcc , logfbank
import librosa as lr
import os, glob, pickle
import librosa
from scipy import signal
import noisereduce as nr
from glob import glob
import librosa
#All the Required Packages and Libraies are installed.
import soundfile
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import accuracy_score

f:\Softwares\Anaconda\lib\site-packages\paramiko\transport.py:219: CryptographyDeprecationWarning: Blowfish has been deprecated
  "class": algorithms.Blowfish,


In [2]:
#Loading the required custom DataSet 
os.listdir(path='F:/VS Code/Minor1_midsem/custom dataset_final') #Loading the Dataset
def getListOfFiles(dirName):
    listOfFile=os.listdir(dirName)
    allFiles=list()
    for entry in listOfFile:
        fullPath=os.path.join(dirName, entry)
        if os.path.isdir(fullPath):
            allFiles=allFiles + getListOfFiles(fullPath)
        else:
            allFiles.append(fullPath)
    return allFiles

dirName = './custom dataset_final'
listOfFiles = getListOfFiles(dirName)
len(listOfFiles)

19487

In [3]:
def envelope(y , rate, threshold):
    mask=[]
    y=pd.Series(y).apply(np.abs)
    y_mean = y.rolling(window=int(rate/10) ,  min_periods=1 , center = True).mean()
    for mean in y_mean:
        if mean>threshold:
            mask.append(True)
        else:
            mask.append(False)
    return mask

In [4]:
#Feature Extraction of Audio Files Function 
#Extract features (mfcc, chroma, mel) from a sound file
def extract_feature(file_name, mfcc, chroma, mel):
    with soundfile.SoundFile(file_name) as sound_file:
        X = sound_file.read(dtype="float32")
        sample_rate=sound_file.samplerate
        if chroma:
            stft=np.abs(librosa.stft(X))
        result=np.array([])
        if mfcc:
            mfccs=np.mean(librosa.feature.mfcc(y=X, sr=sample_rate, n_mfcc=40).T, axis=0)
        result=np.hstack((result, mfccs))
        if chroma:
            chroma=np.mean(librosa.feature.chroma_stft(S=stft, sr=sample_rate).T,axis=0)
        result=np.hstack((result, chroma))
        if mel:
            mel=np.mean(librosa.feature.melspectrogram(X, sr=sample_rate).T,axis=0)
        result=np.hstack((result, mel))
    return result

In [5]:
#Emotions in the RAVDESS dataset to be classified Audio Files based on . 
emotions={
  '01':'neutral',
  '02':'calm',
  '03':'happy',
  '04':'sad',
  '05':'angry',
  '06':'fearful',
  '07':'disgust',
  '08':'surprised'
}
#These are the emotions User wants to observe more :
observed_emotions=['sad', 'happy', 'fear', 'angry', 'disgust', 'neutral']
observed_emotions2=['SAD', 'HAP', 'FEA', 'ANG', 'DIS', 'NEU']

In [6]:
#Load the data and extract features for each sound file
import os
import glob
def load_data(test_size=0.25):
    x,y=[],[]
    answer = 0
    for file in glob.glob(r'F:\VS Code\Minor1_midsem\custom dataset_final\\**\\*.wav'):
        file_name=os.path.basename(file)
        emo=file.split("\\")[4]
        emotion=emo.split(".")[0]
        if emotion not in observed_emotions:
            answer += 1
            continue
        feature=extract_feature(file, mfcc=True, chroma=True, mel=True)
        x.append(feature)
        y.append([emotion,file_name])
    return train_test_split(np.array(x), y, test_size=test_size, random_state=9)

In [8]:
#Split the dataset
import librosa
import numpy as np
x_train,x_test,y_train,y_test=load_data(test_size=0.15)
print(np.shape(x_train),np.shape(x_test), np.shape(y_train),np.shape(y_test))
y_test_map = np.array(y_test).T
y_test = y_test_map[0]
test_filename = y_test_map[1]
y_train_map = np.array(y_train).T
y_train = y_train_map[0]
train_filename = y_train_map[1]
print(np.shape(y_train),np.shape(y_test))
print(*test_filename,sep="\n")

C:\Users\dell\AppData\Local\Temp\ipykernel_26476\2946855648.py:17: FutureWarning: Pass y=[ 0.          0.          0.         ... -0.0206604  -0.00640869
  0.00167847] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mel=np.mean(librosa.feature.melspectrogram(X, sr=sample_rate).T,axis=0)
C:\Users\dell\AppData\Local\Temp\ipykernel_26476\2946855648.py:17: FutureWarning: Pass y=[ 0.          0.          0.         ... -0.3718872  -0.21502686
  0.03527832] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mel=np.mean(librosa.feature.melspectrogram(X, sr=sample_rate).T,axis=0)
C:\Users\dell\AppData\Local\Temp\ipykernel_26476\2946855648.py:17: FutureWarning: Pass y=[ 0.          0.          0.         ...  0.08511353  0.0914917
 -0.00814819] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mel=np.mean(librosa.feature.melspectrogram(X, sr=sample_

(16563, 180) (2924, 180) (16563, 2) (2924, 2)
(16563,) (2924,)
1062_IWW_ANG_XX.wav
1065_IEO_FEA_MD.wav
03-01-06-01-31-121-02-02-02-02.wav
03-02-06-02-37-40-02-01-00-16.wav
YAF_have_happy.wav
03-02-02-01-52-122-02-02-02.wav
03-02-04-01-12-105-02-03-00-14-02.wav
1059_ITH_FEA_XX.wav
1027_IEO_SAD_LO.wav
03-01-04-01-13-100-02-03-00-14-04.wav
1044_WSI_HAP_XX.wav
03-02-07-02-01-02-02-03-01-17.wav
03-02-06-02-62-40-02-01-00-16.wav
JK_n02.wav
YAF_pass_disgust.wav
03-02-04-01-01-49-02-01-00-14.wav
1057_TSI_DIS_XX.wav
1054_IWW_NEU_XX.wav
03-01-04-02-01-01-20.wav
03-02-06-02-77-23-02-01-00-16-77.wav
1032_MTI_ANG_XX.wav
1039_TSI_HAP_XX.wav
KL_n16.wav
03-01-05-01-63-64-02-02-02-01.wav
YAF_wife_happy.wav
1017_MTI_HAP_XX.wav
03-01-03-01-02-81-02-02-04.wav
1055_IWW_SAD_XX.wav
03-02-07-01-05-101-02-02-02-17.wav
1046_TSI_SAD_XX.wav
OAF_puff_disgust.wav
03-02-04-01-40-101-02-01-00-14-03.wav
1049_TIE_HAP_XX.wav
OAF_lot_sad.wav
1011_IWW_HAP_XX.wav
03-02-04-01-70-101-02-01-00-18.wav
03-01-02-01-04-31-02-03-0

In [9]:
#Get the shape of the training and testing datasets
print((x_train.shape[0], x_test.shape[0]))
print((x_train[0], x_test[0]))
#Get the number of features extracted
print(f'Features extracted: {x_train.shape[1]}')

(16563, 2924)
(array([-2.20687103e+02,  7.50503082e+01, -6.97729645e+01, -2.75165005e+01,
       -4.00598564e+01, -4.78651905e+00, -3.33733177e+01, -2.05032825e+01,
        1.11067791e+01, -6.86072683e+00,  1.15450907e+01,  3.45467281e+00,
       -1.71346416e+01,  1.87046375e+01,  1.46700687e+01, -1.07165966e+01,
       -6.80783319e+00,  8.71929109e-01, -1.95320473e+01,  2.38100266e+00,
       -5.08501196e+00, -8.48231506e+00, -5.58877516e+00,  7.61446524e+00,
       -9.64068222e+00,  9.00738716e+00, -8.83144283e+00, -1.32687628e+00,
        4.86759853e+00, -8.24091530e+00,  1.20521522e+00, -3.77609181e+00,
       -2.94654083e+00, -9.77812707e-01, -5.50790119e+00, -2.97175837e+00,
       -5.91586065e+00, -1.22827613e+00, -4.55804348e+00, -2.84986281e+00,
        3.87070090e-01,  3.51830512e-01,  3.35551322e-01,  3.16911846e-01,
        3.60632867e-01,  4.51232642e-01,  3.92683536e-01,  3.57939363e-01,
        4.51888233e-01,  5.04385650e-01,  4.29880589e-01,  3.74721974e-01,
        2.

In [10]:

# Initialize the Multi Layer Perceptron Classifie
model=MLPClassifier(alpha=0.01, batch_size=256, epsilon=1e-08, hidden_layer_sizes=(300,), learning_rate='adaptive', max_iter=500)

In [11]:
#Train the model
model.fit(x_train,y_train)

MLPClassifier(alpha=0.01, batch_size=256, hidden_layer_sizes=(300,),
              learning_rate='adaptive', max_iter=500)

In [12]:

#SAVING THE MODEL
import pickle
# Save the Modle to file in the current working directory
#For any new testing data other than the data in dataset

Pkl_Filename = "F:/VS Code/Minor1_midsem/SER_by_NOR.pkl"  

with open(Pkl_Filename, 'wb') as file:  
    pickle.dump(model, file)

In [13]:
# Load the Model back from file
with open(Pkl_Filename, 'rb') as file:  
    Speech_Emotion_Recognition = pickle.load(file)

Speech_Emotion_Recognition

MLPClassifier(alpha=0.01, batch_size=256, hidden_layer_sizes=(300,),
              learning_rate='adaptive', max_iter=500)

In [14]:
#predicting :
y_pred=Speech_Emotion_Recognition.predict(x_test)
y_pred

array(['angry', 'disgust', 'angry', ..., 'fear', 'neutral', 'neutral'],
      dtype='<U7')

In [15]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix
result = confusion_matrix(y_test, y_pred)
print("Confusion Matrix:")
print(result)
print('Accuracy Score :',accuracy_score(y_test, y_pred))
print('Report : ')
print(classification_report(y_test, y_pred))

Confusion Matrix:
[[271  61  22  73  18  20]
 [ 23 270  11  36  39  43]
 [ 23  54 205  46  20  62]
 [ 50 101  39 302  34  42]
 [ 11 113   6  47 245  68]
 [ 21  85   7  50  48 358]]
Accuracy Score : 0.5646374829001368
Report : 
              precision    recall  f1-score   support

       angry       0.68      0.58      0.63       465
     disgust       0.39      0.64      0.49       422
        fear       0.71      0.50      0.59       410
       happy       0.55      0.53      0.54       568
     neutral       0.61      0.50      0.55       490
         sad       0.60      0.63      0.62       569

    accuracy                           0.56      2924
   macro avg       0.59      0.56      0.57      2924
weighted avg       0.59      0.56      0.57      2924



In [16]:
#Store the Prediction probabilities into CSV file 
import numpy as np
import pandas as pd
y_pred1 = pd.DataFrame(y_pred, columns=['predictions'])
y_pred1['file_names'] = test_filename
print(y_pred1)
y_pred1.to_csv('predictions_custon_data_final.csv')

     predictions                            file_names
0          angry                   1062_IWW_ANG_XX.wav
1        disgust                   1065_IEO_FEA_MD.wav
2          angry    03-01-06-01-31-121-02-02-02-02.wav
3           fear     03-02-06-02-37-40-02-01-00-16.wav
4          happy                    YAF_have_happy.wav
...          ...                                   ...
2919        fear  03-02-06-02-17-25-02-01-00-16-77.wav
2920       happy                  OAF_hole_neutral.wav
2921        fear     03-02-02-01-01-25-02-01-00-24.wav
2922     neutral       03-01-02-01-06-100-04-02-02.wav
2923     neutral     03-01-02-01-10-28-01-02-02-01.wav

[2924 rows x 2 columns]
